Mit Binder oder Colab kann das Jupyter-Notebook interaktiv im Browser gestartet werden:

[![Open In Colab](https://colab.research.google.com/assets/colab-badge.svg)](https://colab.research.google.com/github/opendatazurich/opendatazurich.github.io/blob/master/geoportal/Geoportal_3d_blockmodell_lod1.ipynb)

[![Binder](https://mybinder.org/badge_logo.svg)](https://mybinder.org/v2/gh/opendatazurich/opendatazurich.github.io/master?labpath=geoportal%2FGeoportal_3d_blockmodell_lod1.ipynb)

# LOD1 3D Blockmodell via WFS beziehen

Ein WFS-Dienst liefert Vektor-Geodaten. Überlicherweise sind bei einem WFS mehrere Layer enthalten, welche jeweils unterschiedliche Daten enthalten können. [Esri hat eine gute Anleitung](https://enterprise.arcgis.com/de/server/10.3/publish-services/linux/communicating-with-a-wfs-service-in-a-web-browser.htm), wie mit einem WFS-Server kommuniziert werden kann.

In diesem Notebook wird gezeigt, wie 3D-Blockmodell-Geodaten via WFS abgefragt und gespeichert werden können (z.B. als GeoJSON). Die Daten können dabei auf einer Karte dargestellt werden, oder auch als tabellarische Daten aufbereitet werden.

Hinweis: die URL zum WFS Dienst finden man via Geoportal, welches auf dem OGD-Katalog auf den Geo-Datensätzen verlinkt ist.

In [52]:
#%pip install geopandas requests folium

In [53]:
import xml.etree.ElementTree as ET

import geopandas
import requests
import folium

In [54]:
wfs_url = "https://www.ogd.stadt-zuerich.ch/wfs/geoportal/3D_Blockmodell_LoD1"

## GetCapabilities

In [55]:
# GetCapabilities zeigt die möglichen Anfragen an einen WFS-Server
r = requests.get(wfs_url, params={
    'service': 'WFS',
    'version': '1.0.0',
    'request': 'GetCapabilities'
})
r.content


b'<WFS_Capabilities xmlns:xsi="http://www.w3.org/2001/XMLSchema-instance" xmlns:gml="http://www.opengis.net/gml" xmlns:xlink="http://www.w3.org/1999/xlink" xmlns="http://www.opengis.net/wfs" xsi:schemaLocation="http://www.opengis.net/wfs http://schemas.opengis.net/wfs/1.0.0/WFS-capabilities.xsd" version="1.0.0" xmlns:ogc="http://www.opengis.net/ogc" updateSequence="0" xmlns:ows="http://www.opengis.net/ows">\n <Service>\n  <Name>WFS</Name>\n  <Title>Untitled</Title>\n  <OnlineResource/>\n </Service>\n <Capability>\n  <Request>\n   <GetCapabilities>\n    <DCPType>\n     <HTTP>\n      <Get onlineResource="https://www.ogd.stadt-zuerich.ch/wfs/geoportal/3D_Blockmodell_LoD1"/>\n     </HTTP>\n    </DCPType>\n    <DCPType>\n     <HTTP>\n      <Post onlineResource="https://www.ogd.stadt-zuerich.ch/wfs/geoportal/3D_Blockmodell_LoD1"/>\n     </HTTP>\n    </DCPType>\n   </GetCapabilities>\n   <DescribeFeatureType>\n    <SchemaDescriptionLanguage>\n     <XMLSCHEMA/>\n    </SchemaDescriptionLanguage

In [56]:
# XML parsen und die Layer-Informationen extrahieren
root = ET.fromstring(r.content)
namespaces = {
    'wfs': 'http://www.opengis.net/wfs'
}
layers = {}
for feature_type in root.findall('wfs:FeatureTypeList/wfs:FeatureType', namespaces):
    layers[feature_type.find('wfs:Name', namespaces).text] = {
        'srs': feature_type.find('wfs:SRS', namespaces).text,
    }

layers

{'lod1_2_5d': {'srs': 'EPSG:2056'},
 'lod1_bruecke_max_3d': {'srs': 'EPSG:2056'},
 'lod1_bruecke_min_3d': {'srs': 'EPSG:2056'},
 'lod1_gebaeude_max_3d': {'srs': 'EPSG:2056'},
 'lod1_gebaeude_min_3d': {'srs': 'EPSG:2056'}}

Ich möchte im Folgenden den Layer **lod1_gebaeude_max_3d** abfragen. Die Details zu den einzelnen Layern sind auf dem OGD-Katalog beschrieben oder direkt auf geocat.ch.

Beispiel: https://www.stadt-zuerich.ch/geodaten/download/3D_Blockmodell_LoD1 und auf [Geocat](https://www.geocat.ch/geonetwork/srv/ger/catalog.search#/metadata/1c949aaf-7984-8a01-865c-91a9bc35a489/formatters/xsl-view?root=div&view=advanced)

In [57]:
# Prüfen, welche Formate GetFeature bietet
formats = root.find('wfs:Capability/wfs:Request/wfs:GetFeature/wfs:ResultFormat', namespaces)
for child in formats:
    print(child.tag)

{http://www.opengis.net/wfs}GML2
{http://www.opengis.net/wfs}GML3
{http://www.opengis.net/wfs}GeoJSON


## LOD1-Daten via GetFeature als GeoJSON laden

In [58]:
# Yay, GeoJSON!
# Daten als GeoJSON holen
layer = 'lod1_gebaeude_max_3d'

r = requests.get(wfs_url, params={
    'service': 'WFS',
    'version': '1.0.0',
    'request': 'GetFeature',
    'typename': layer,
    'outputFormat': 'GeoJSON'
})
lod1 = r.json()

### Daten in GeoPandas einlesen (Geodataframe)

Projektionen:
 - .to_crs(epsg=4326): WGS84
 - .to_crs(epsg=2056): LV95

In [59]:
# load GeoJSON in geopandas
srs = layers[layer]['srs']
gdf_lod1 = geopandas.GeoDataFrame.from_features(lod1, crs=srs)

In [60]:
#eingelesene Projektion
gdf_lod1.crs

<Projected CRS: EPSG:2056>
Name: CH1903+ / LV95
Axis Info [cartesian]:
- E[east]: Easting (metre)
- N[north]: Northing (metre)
Area of Use:
- name: Europe - Liechtenstein and Switzerland
- bounds: (5.96, 45.82, 10.49, 47.81)
Coordinate Operation:
- name: Swiss Oblique Mercator 1995
- method: Hotine Oblique Mercator (variant B)
Datum: CH1903+
- Ellipsoid: Bessel 1841
- Prime Meridian: Greenwich

In [61]:
# wenn ich die crs wecheln will kann ich das über .to_crs() machen.
# Achtung, dauert für alle Daten recht lange...

#gdf_lod1_wgs84 = gdf_lod1.to_crs(epsg=4326)
#gdf_lod1_wgs84.crs

In [62]:
gdf_lod1.head(2)

geometry      adat  art  \
0  MULTIPOLYGON Z (((8.54140 47.37494 405.70000, ...  20140925    0   
1  MULTIPOLYGON Z (((8.51059 47.42538 448.60000, ...  20220428   13   

        ausr     bem    dach      edat         egid filt  \
0  BATCHUSER  OKMESS  6000.0  20090101    2372735.0   08   
1     GEORUR  OKMESS  6000.0  20140526  302031659.0   01   

                      gid_3d  h_boden  h_first  h_mean  h_rel_first_boden  \
0  z41ac39cc00001a74-00-0001    405.7    416.3   416.3               10.6   
1  z49c8da4300000031-00-0001    448.6    448.9   448.9                0.3   

   h_trauf               ogid otype qumess   sta wichtig  
0    416.3  z41ac39cc00001a74    BB   None  real    None  
1    448.9  z49c8da4300000031    EO   None  real    None

### Pagination

Falls ein WFS sehr viele Daten zurückliefert, ist es auch möglich mit Pagination jeweils nur einen Teil der Daten zu beziehen. Dazu dienen die beiden Parameter `startIndex` und `maxFeatures`.

Um Informationen zu den Resultaten zu bekommen, kann ein GetFeature-Request mit dem `resultType` **hits** gemacht werden:

In [63]:
# Start bei Index 5 (`startIndex=5`), d.h. 0-4 werden ausgelassen und holen 1 Feature (`maxFeatures=1`)
r = requests.get(wfs_url, params={
    'service': 'WFS',
    'version': '1.0.0',
    'request': 'GetFeature',
    'typename': layer,
    'resultType': 'hits'
})
r.content

b'<wfs:FeatureCollection xmlns:wfs="http://www.opengis.net/wfs" xmlns:ogc="http://www.opengis.net/ogc" xmlns:gml="http://www.opengis.net/gml" xmlns:ows="http://www.opengis.net/ows" xmlns:xlink="http://www.w3.org/1999/xlink" xmlns:qgs="http://www.qgis.org/gml" xmlns:xsi="http://www.w3.org/2001/XMLSchema-instance" xsi:schemaLocation="http://www.opengis.net/wfs http://schemas.opengis.net/wfs/1.0.0/wfs.xsd http://www.qgis.org/gml https://www.ogd.stadt-zuerich.ch/wfs/geoportal/3D_Blockmodell_LoD1?SERVICE=WFS&amp;VERSION=1.0.0&amp;REQUEST=DescribeFeatureType&amp;TYPENAME=lod1_gebaeude_max_3d&amp;OUTPUTFORMAT=XMLSCHEMA"\n timeStamp="2024-02-07T16:09:13"\n numberOfFeatures="60070">\n</wfs:FeatureCollection>'

In [72]:
# Start bei Index 5 (`startIndex=5`), d.h. 0-4 werden ausgelassen und holen 4 Feature (`maxFeatures=4`)
r = requests.get(wfs_url, params={
    'service': 'WFS',
    'version': '1.0.0',
    'request': 'GetFeature',
    'typename': layer,
    'outputFormat': 'GeoJSON',
    'startIndex': 5,
    'maxFeatures': 1000
})
first_page = r.json()


### GeoJson auf die Karte bringen

Mit Folium können die eben ausgewählten Ausschnitte als GeoJSON auf Leaflet dargestellt werden.

In [73]:
m = folium.Map(location=[47.38, 8.53], zoom_start=13)
folium.GeoJson(first_page).add_to(m)
m

### Daten in Karte integrierten

In [67]:
# Basiskarte mit GeoJSON layer
m = folium.Map(location=[47.38, 8.53], zoom_start=13, tiles=None)
folium.raster_layers.WmsTileLayer(
    url='https://www.ogd.stadt-zuerich.ch/wms/geoportal/Basiskarte_Zuerich_Raster_Grau',
    layers='Basiskarte_Zuerich_Raster_Grau',
    name='Zürich - Basiskarte',
    fmt='image/png',
    overlay=False,
    control=False,
    autoZindex=False,
).add_to(m)
folium.features.GeoJson(first_page).add_to(m)
m